Copyright **`(c)`** 2023 Giovanni Squillero `<giovanni.squillero@polito.it>`  
[`https://github.com/squillero/computational-intelligence`](https://github.com/squillero/computational-intelligence)  
Free for personal or classroom use; see [`LICENSE.md`](https://github.com/squillero/computational-intelligence/blob/master/LICENSE.md) for details.  

# LAB9

Write a local-search algorithm (eg. an EA) able to solve the *Problem* instances 1, 2, 5, and 10 on a 1000-loci genomes, using a minimum number of fitness calls. That's all.

### Deadlines:

* Submission: Sunday, December 3 ([CET](https://www.timeanddate.com/time/zones/cet))
* Reviews: Sunday, December 10 ([CET](https://www.timeanddate.com/time/zones/cet))

Notes:

* Reviews will be assigned  on Monday, December 4
* You need to commit in order to be selected as a reviewer (ie. better to commit an empty work than not to commit)

In [46]:
from random import choices, randint, choice, sample, random
from copy import copy, deepcopy

import lab9_lib
import numpy as np
import math


In [47]:
fitness = lab9_lib.make_problem(1)
for n in range(10):     #Determina il numero di Fitness call
    ind = choices([0, 1], k=1000)     #genoma casuale di 50 elementi
    print(f"{''.join(str(g) for g in ind)}: {fitness(ind):.2%}")

print(fitness.calls)

1110011101100010001110101111000010011001010000011010111111101010111000011100000010100101001101010110101110101111011000010011100101111001110011000000110100100011101101110001100010000010010100010001101001011001010100010101011110111010000100000101101011011110010000011101101010100011010010010101011111100110111101000110001011011011100011110010101111001100110011100011011000011100001010001001000011010110110010100001110001110010100100011000001010011001011010011010110000101000010010101100000101011001000111100000110000111001000111100101010101101110110000000000000100110010011000000111000011111011010010011100010001001010000101011001011001100010011100000010011001011011110011010101100000000011010110011110011001000100101101110101000011001010000100110000111100010010001010111011110101001111010100011001101100010000100101111011011111100101000001010110000101001110100001000010100010101000100100001100011101010001100110000110101100101010101111101011010110011000111110110110010000011100111001110111100101110100

# Local Search Algorithm

### Mutation Techniques

In [48]:
def mutation1(ind):     # 1 loci(gene) mutated
    offspring = copy(ind)
    pos = randint(0, NUM_LOCI-1)
    offspring[pos] = 1 - offspring[pos]     # Se ho T/F-> offspring[pos] = not offspring[pos]
    #assert len(offspring) == NUM_LOCI
    return offspring

def mutation2(ind):     # Reset randomly a random number of loci
    offspring = copy(ind)
    poss = (randint(0, NUM_LOCI-1), randint(0, NUM_LOCI-1))
    offspring = ind[:min(poss)] + [choice([0, 1])for _ in range(max(poss)-min(poss))] + ind[max(poss):]
    #assert len(offspring) == NUM_LOCI

    return offspring

### Recombination Techniques

In [49]:
def one_cut_crossover(ind1, ind2):
    cut_point = randint(0, NUM_LOCI-1)
    offspring = ind1[:cut_point] + ind2[cut_point:]
    #    assert len(offspring) == NUM_LOCI
    return offspring

def two_cut_crossover(ind1, ind2):
    cut_points = (randint(0, NUM_LOCI-1), randint(0, NUM_LOCI-1))
    offspring = ind1[:min(cut_points)] + ind2[min(cut_points) : max(cut_points)] + ind1[max(cut_points):]
    
    assert len(offspring) == NUM_LOCI
    return offspring

def uniform_crossover(ind1, ind2):
    offspring = [ind1[i] if i % 2 else ind2[i] for i in range(NUM_LOCI)]
    # assert len(offspring) == NUM_LOCI
    return offspring

def uniform_crossover_double(ind1, ind2):
    o1, o2 = ([ind1[i] if i % 2 else ind2[i] for i in range(NUM_LOCI)], [ind2[i] if i % 2 else ind1[i] for i in range(NUM_LOCI)])
    # assert len(offspring) == NUM_LOCI
    return o1, o2

### Parent Selection

In [65]:
def roulette_wheel(population):     # Roulette wheel with same probability
    return choice(population)[0]

def variable_tournament(population):
    
    n_partecipants = randint(2, int(len(population)/2))
    pool = choices(population, k=n_partecipants)
    parent = max(pool, key=lambda ind: ind[1])

    return parent[0]

def static_tournament(pop):

    pool = [choice(pop) for _ in range(TOURNAMENT_SIZE)]
    champ = max(pool, key=lambda ind: ind[1])
    
    return champ[0]

def best_parent_ever(population):
    champ = max(population, key=lambda ind: ind[1])
    return champ[0]

def genotype_screening(population):     # Select the 2 element with most differnt genotype 
    distance = []
    for i in range(len(population)):
        distance.append([sum(np.bitwise_xor(np.array(population[i][0]), np.array(population[j][0]))) for j in range(len(population))])
    
    distance = np.array(distance)
    max_position = np.unravel_index(np.argmax(distance, axis=None), distance.shape)
    
    return population[max_position[0]][0], population[max_position[1]][0]

### Survival Selection

In [51]:
def survival_selection(population):
    population.sort(key=lambda ind: ind[1], reverse=True)       # ORDERING FROM BEST TO WORSE
    return population[:POPULATION_SIZE]       # SURVIVAL SELECTION
    
def remove_twin(population):        # Remove TWIN from the population because I belive that they will have the same fitness
    twins = set()
    for i in range(len(population)):
        for j in range(i+1, len(population)):
            if population[i]==population[j]:
                twins.add(j)
    
    new_p = [ind for i, ind in enumerate(population) if i not in twins]
    return new_p

## Problem start from HERE ->

In [68]:
# GLOBAL PARAMETER #
NUM_LOCI = 1000

POPULATION_SIZE = 10
NEW_OFFSPRING = 30
TOURNAMENT_SIZE = 5
MUTATION_PROBABILITY = .15

# . . . . . . #

fitness = lab9_lib.make_problem(1)
starting_population = [choices([0, 1], k=NUM_LOCI) for _ in range(POPULATION_SIZE)]

In [69]:
population = [(ind, fitness(ind)) for ind in starting_population]

mutation_strategy = (mutation1, mutation2)
recombination_strategy = (one_cut_crossover, uniform_crossover)
parent_selection_strategy = (roulette_wheel, static_tournament, variable_tournament)
survival_selection_strategy = (remove_twin, survival_selection)

while all(ind[1] != 1 for ind in population):     # condizione da sistemare
    offspring = list()
    
    p1, p2 = genotype_screening(population)
    o1, o2 =  uniform_crossover_double(p1, p2)    
    population.extend([(o1, fitness(o1)), (o2, fitness(o2))])

    for counter in range(NEW_OFFSPRING):
        if random() < MUTATION_PROBABILITY:
            # MUTATION 
            p = choice(parent_selection_strategy)(population)
            o = choice(mutation_strategy)(p)
        else:
            #CROSS-OVER
            p1 = choice(parent_selection_strategy)(population)
            p2 = choice(parent_selection_strategy)(population)
            o =  choice(recombination_strategy)(p1, p2)
        offspring.append((o, fitness(o)))

    population.extend(offspring)
    population = remove_twin(population)
    population = survival_selection(population)

    print(population[0][1], population[0][0])
print(fitness.calls)

0.53 [0, 0, 0, 1, 1, 1, 1, 1, 1, 0, 1, 1, 1, 1, 1, 0, 0, 1, 1, 1, 0, 1, 0, 1, 0, 1, 1, 0, 1, 1, 0, 1, 0, 1, 1, 1, 0, 0, 1, 1, 1, 1, 0, 1, 0, 1, 1, 0, 1, 0, 0, 1, 1, 1, 1, 0, 1, 0, 0, 1, 1, 0, 0, 0, 1, 1, 0, 0, 0, 0, 1, 1, 0, 1, 1, 0, 1, 1, 0, 0, 1, 1, 0, 1, 1, 1, 1, 0, 0, 0, 1, 0, 0, 1, 0, 1, 0, 0, 1, 0, 1, 1, 0, 1, 0, 0, 0, 0, 1, 1, 0, 1, 1, 1, 0, 1, 1, 0, 1, 0, 1, 1, 0, 1, 0, 0, 1, 1, 1, 1, 1, 0, 0, 1, 1, 1, 0, 1, 1, 1, 0, 1, 0, 0, 0, 1, 1, 1, 1, 0, 1, 1, 1, 1, 1, 0, 0, 1, 0, 1, 0, 0, 1, 1, 1, 1, 0, 1, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 1, 1, 0, 0, 1, 1, 1, 1, 1, 0, 0, 0, 0, 1, 0, 1, 1, 1, 1, 0, 0, 0, 0, 1, 1, 1, 1, 1, 1, 1, 0, 1, 1, 1, 0, 1, 0, 0, 0, 0, 1, 1, 0, 0, 1, 1, 0, 0, 0, 0, 1, 1, 1, 0, 0, 1, 0, 1, 1, 1, 1, 0, 0, 0, 0, 1, 0, 0, 1, 1, 0, 0, 0, 1, 0, 0, 1, 1, 1, 0, 0, 1, 1, 0, 1, 0, 1, 0, 0, 1, 0, 0, 1, 0, 1, 1, 0, 0, 0, 0, 0, 1, 1, 1, 1, 1, 1, 1, 0, 0, 0, 0, 0, 0, 1, 0, 1, 1, 0, 1, 1, 1, 0, 0, 0, 0, 0, 1, 0, 0, 0, 1, 0, 0, 0, 0, 1, 1, 1, 1, 1, 0, 0, 0, 1, 0, 0, 0, 1, 0, 0, 1, 1, 1